In [4]:
import torch
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import DataLoader, TensorDataset
import numpy as np
import pandas as pd

In [5]:
# code adapted from ChatGPT

# Define your neural network model
class SimpleModel(nn.Module):
    def __init__(self):
        super(SimpleModel, self).__init__()

        self.step1 = nn.Linear(2, 128, bias=True)
        self.step2 = nn.ReLU()
        self.step3 = nn.Linear(128, 64, bias=True)
        self.step4 = nn.ReLU()
        self.step5 = nn.Linear(64, 16, bias=True)
        self.step6 = nn.ReLU()
        self.step7 = nn.Linear(16, 1, bias=True)
        self.step8 = nn.Sigmoid()

    def forward(self, x):

        # RUN IT ON A GPU if it exists
        if torch.cuda.is_available():
            x = x.to("cuda")

        x = self.step1(x)
        x = self.step2(x)
        x = self.step3(x)
        x = self.step4(x)
        x = self.step5(x)
        x = self.step6(x)
        x = self.step7(x)
        x = self.step8(x)
        
        return x

def train_model(inputs, desired_outputs, num_epochs=100, learning_rate=0.02, momentum=0.9):
    # Convert inputs and desired_outputs to PyTorch tensors
    inputs = torch.tensor(inputs, dtype=torch.float32)
    desired_outputs = torch.tensor(desired_outputs, dtype=torch.float32)
    
    # Create a DataLoader to handle batching (if needed)
    dataset = TensorDataset(inputs, desired_outputs)
    dataloader = DataLoader(dataset, batch_size=1000, shuffle=True)  # Adjust batch_size as needed
    
    # Initialize the model
    model = SimpleModel()
    
    # Define loss function and optimizer
    criterion = nn.MSELoss()  # Mean Squared Error loss
    optimizer = optim.SGD(model.parameters(), lr=learning_rate, momentum=momentum)
    
    # Training loop
    for epoch in range(num_epochs):
        total_loss = 0.0
        for batch_inputs, batch_desired_outputs in dataloader:
            optimizer.zero_grad()  # Zero the gradients
            outputs = model(batch_inputs)  # Forward pass
            loss = criterion(outputs, batch_desired_outputs)  # Compute the loss
            loss.backward()  # Backpropagation
            optimizer.step()  # Update the model's parameters
            cur_item = loss.item()
            total_loss += cur_item
        
        # Print the average loss for this epoch
        print(f"total loss: {total_loss}")
        average_loss = total_loss / len(dataloader)
        for i, param in model.named_parameters():
            print(param)
        print(f'Epoch [{epoch+1}/{num_epochs}], Loss: {average_loss:.4f}')
    
    # Return the trained model
    return model

In [6]:
input_data = np.random.randint(1, 100, size=(1000, 2))
desired_output = []

for i in input_data:
    desired_output.append([int(i[0] < i[1])])
    
# Train the model
trained_model = train_model(input_data, desired_output, 500)


total loss: 0.3425861895084381
Parameter containing:
tensor([[-2.5154e-02, -4.8168e-01],
        [ 5.7037e-01,  3.7239e-01],
        [-2.7187e-01,  6.6313e-01],
        [ 1.5683e-01,  3.9668e-01],
        [-5.0581e-02,  3.2091e-01],
        [ 4.5735e-01,  6.2984e-01],
        [ 5.2435e-01, -5.0970e-01],
        [-2.3643e-02,  6.9237e-01],
        [ 2.3734e-01,  1.2571e-01],
        [-1.7239e-01,  2.4071e-01],
        [ 6.5681e-01, -5.0195e-01],
        [ 6.6552e-01, -1.9082e-01],
        [ 1.6691e-01,  3.8879e-01],
        [ 4.5705e-01,  3.2147e-01],
        [-1.0323e-01, -3.9313e-01],
        [ 6.8385e-01,  9.3602e-02],
        [-5.2502e-01, -5.9574e-01],
        [ 2.6653e-01, -9.4698e-02],
        [-5.9514e-01,  2.5206e-01],
        [-6.5929e-01,  6.6883e-02],
        [ 5.2373e-01,  2.9602e-01],
        [-6.2549e-01, -3.3254e-01],
        [ 6.2949e-01, -9.4760e-02],
        [-9.8978e-03,  2.3981e-02],
        [ 4.9263e-02, -2.4487e-01],
        [-1.8576e-01,  1.6725e-01],
        [ 1

In [7]:
def test_model(model, new_data, expected_result):
    test_input = torch.tensor(new_data, dtype=torch.float32)
    test_output = trained_model(test_input)

    # apply the step function with the step at 0.5 to decide whether to predict 1 or 0 for this element
    predicted_classes = torch.tensor(test_output + 0.5, dtype=torch.int)
    test_output_compare = torch.tensor(expected_result, dtype=torch.int)

    diff = abs(predicted_classes - test_output_compare)
    accuracy = 1 - ((sum(diff)) / len(test_input))
    return float(accuracy)

In [8]:
test_input = np.random.randint(1, 10000, size=(500, 2))
test_output_compare = []

for i in test_input:
    test_output_compare.append([int(i[0] < i[1])])

test_model(trained_model, test_input, test_output_compare)

C:\Users\16089\AppData\Local\Temp\ipykernel_26304\1059146562.py:6: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  predicted_classes = torch.tensor(test_output + 0.5, dtype=torch.int)


0.9980000257492065

In [72]:
for i, param in trained_model.named_parameters():
    print(i)
    print(param)

step1.weight
Parameter containing:
tensor([[ 0.5953, -0.2124],
        [ 0.6483, -0.4034],
        [-0.5812, -0.0748],
        [-0.5560,  0.4902],
        [ 0.4897, -0.6016],
        [-0.5551, -0.2022],
        [ 0.5587, -0.4411],
        [-0.4963, -0.2022],
        [ 0.3546,  0.1487],
        [ 0.3233, -0.0672],
        [-0.3599, -0.0984],
        [ 0.1046, -0.3002],
        [-0.6460,  0.0064],
        [ 0.5361,  0.0046],
        [-0.3434, -0.1991],
        [-0.4925,  0.3047],
        [ 0.0134, -0.0891],
        [-0.1875, -0.0684],
        [ 0.3123,  0.1871],
        [ 0.5256,  0.6629],
        [-0.2258, -0.2291],
        [-0.1662, -0.5283],
        [ 0.5589, -0.5020],
        [-0.5499,  0.3628],
        [ 0.4896, -0.3307],
        [-0.6173, -0.1205],
        [-0.2480, -0.0067],
        [-0.7021,  0.2324],
        [ 0.6068,  0.0980],
        [-0.0336, -0.3352],
        [-0.0688,  0.2136],
        [ 0.0904,  0.4197],
        [ 0.3930,  0.5942],
        [-0.3101,  0.5294],
        [-0.5

In [19]:
# test the neural network with the data points from data.csv
df = pd.read_csv("data.csv")

df_input = np.random.randint(1, 100, size=(len(df), 2))

In [20]:
for i in range(0, len(df_input)):
    df_input[i][0] = df['val1'][i]
    df_input[i][1] = df['val2'][i]

In [21]:
df_input

array([[ 17,  31],
       [137, 517],
       [ 85, 154],
       ...,
       [ 55,  89],
       [256, 365],
       [124, 211]])

In [24]:
df_classificaitons = []
for i in range(0, len(df['last_matrix_was_U'])):
    df_classificaitons.append([1-df["last_matrix_was_U"][i]])

In [25]:
test_model(trained_model, df_input, df_classificaitons)

C:\Users\16089\AppData\Local\Temp\ipykernel_26304\1059146562.py:6: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  predicted_classes = torch.tensor(test_output + 0.5, dtype=torch.int)


1.0